In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [7]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'
# stats_file = 'stats_everything' # 'stats_samples'
# target_file = 'target_everything' # 'target_samples'
stats_md_file = 'stats_onlymd' # 'stats_samples'
target_md_file = 'target_onlymd' # 'stats_samples'

In [8]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)
    
with open(os.path.join(working, stats_md_file+'.pickle'), 'rb') as fi:
    stats_md = pickle.load(fi)
    
with open(os.path.join(working, target_md_file+'.pickle'), 'rb') as fi:
    targets_md = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [9]:
def downselect(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [55]:
pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.5, 2.8663175, 3.1,  3.5,  4.5]

In [56]:
stats = downselect(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])
stats_select_md = downselect(stats_md, pair_knots, edens_knots)
print(stats_select_md['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}
{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}


In [57]:
targets['md'] = targets_md['md']
stats['md'] = stats_select_md['md']

In [58]:
for key in sorted(targets.keys()):
    for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
        n = len(xyz)
        vol = np.linalg.det(box)
        corr = float(n*n)/vol
        ene.append([corr])

In [59]:
stats['bcc_npt_langevin_300K']['energy'][0][:]

[array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.32452672e-04,   2.40108437e-01,   1.49699018e+01,
          3.67830273e+01,   6.58053659e+01,   2.44033647e+02,
          4.40325883e+02,   6.80111008e+02,   1.13544979e+03,
          1.32771865e+03,   1.53444986e+03,   1.82571708e+03,
          1.89696652e+03,   1.96972937e+03]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.37184093e-15,   3.18476767e-07,   2.82775234e-02,
          9.17736776e-01,   9.14748666e+00,   1.69749763e+03,
          1.79543454e+04,   1.02110145e+05,   7.92918644e+05,
          1.48233268e+06,   2.64426772e+06,   5.29910283e+06,
          6.17592659e+06,   7.17934901e+06]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          9.35076567e-08,   2.01440000e-03,   1.80322649e+00,
          1.06606591e+01,   3.39604107e+01,   4.65546847e+02,
          1.51515052e+03,   3.61420678e+03,   1.00729590e+04,
          1.37729635e+04,   1.83956954e+

In [60]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [61]:
targets.keys()

['bcc_npt_langevin_3700K',
 'md',
 'vac_npt_langevin_2000K',
 'relax',
 'screw_111_npt_langevin_2000K',
 'bcc_npt_langevin_300K',
 'i111_npt_langevin_2000K',
 'eos',
 'fcc_npt_langevin_300K',
 'eos_fcc',
 'i110_npt_langevin_2000K',
 'liq_3700K',
 'liq_5000K',
 'eos_bcc',
 'bain']

In [62]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 1.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.0),
 ('bain', 0.0)]

In [65]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])

# start_params.append([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
#          3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
#         -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
#         -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
#          7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
#         -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
#          1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
#          2.18327852e+00,   6.63152141e-02, 0.0])

# start_params.append([ -2.95016477e+00,   3.78177969e-04,  -5.21095611e+02,
#          3.09845244e+02,  -4.69222440e+02,   3.95186037e+02,
#         -1.11630659e+02,   5.36915127e+00,   1.52984702e+01,
#         -1.54915170e+01,   7.53107481e+00,  -2.98591742e+00,
#          7.55346307e-01,  -1.00678488e+00,   1.96634582e+00,
#         -8.71560927e-01,  -1.41820832e-01,  -1.46508000e+00,
#          1.42936365e+00,   7.23805795e+01,   0.0, 9.18071460e-01,
#          2.04259992e+00,   6.28575567e-02,   7.62804667e-03])

start_params.append([ -3.27882058e+00,  -9.77681860e-04,  -5.95486537e+02,
         3.42401535e+02,  -4.15497479e+02,   3.71316746e+02,
        -1.07274610e+02,  -2.93282898e+00,   1.51298572e+01,
        -1.37454674e+01,   8.16724633e+00,  -3.16850352e+00,
         8.74607042e-01,  -1.07878768e+00,   1.97939820e+00,
        -8.26149646e-01,  -1.62437297e-01,  -1.45694910e+00,
         1.42153527e+00,   1.29203135e+02,  -9.25284676e+00,
         2.63967417e+00,   2.06410900e+00,   6.03258240e-02*2])

multi_pars = start_params
print(multi_pars)

[[-3.27882058, -0.00097768186, -595.486537, 342.401535, -415.497479, 371.316746, -107.27461, -2.93282898, 15.1298572, -13.7454674, 8.16724633, -3.16850352, 0.874607042, -1.07878768, 1.9793982, -0.826149646, -0.162437297, -1.4569491, 1.42153527, 129.203135, -9.25284676, 2.63967417, 2.064109, 0.120651648]]


In [66]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-3.27882058, -0.00097768186, -595.486537, 342.401535, -415.497479, 371.316746, -107.27461, -2.93282898, 15.1298572, -13.7454674, 8.16724633, -3.16850352, 0.874607042, -1.07878768, 1.9793982, -0.826149646, -0.162437297, -1.4569491, 1.42153527, 129.203135, -9.25284676, 2.63967417, 2.064109, 0.120651648])
loss 9.26277774779e-05 9.26277774779e-05 0.0
('Best params:', [(9.262777747789823e-05, [-3.27882058, -0.00097768186, -595.486537, 342.401535, -415.497479, 371.316746, -107.27461, -2.93282898, 15.1298572, -13.7454674, 8.16724633, -3.16850352, 0.874607042, -1.07878768, 1.9793982, -0.826149646, -0.162437297, -1.4569491, 1.42153527, 129.203135, -9.25284676, 2.63967417, 2.064109, 0.120651648])])
('ieam:', 0)
loss 9.26277774779e-05 9.26277774779e-05 0.0
loss 0.00268428930364 0.00268428930364 0.0
loss 0.000113782352091 0.000113782352091 0.0
loss 9.26174014655e-05 9.26174014655e-05 0.0
loss 8.84576200015e-05 8.84576200015e-05 0.0
loss 0.000149048881183 0.000149048881183 0.0


loss 3.33237981137e-05 3.33237981137e-05 0.0
loss 4.86763316656e-05 4.86763316656e-05 0.0
loss 6.68894373421e-05 6.68894373421e-05 0.0
loss 3.13055103942e-05 3.13055103942e-05 0.0
loss 6.63062931893e-05 6.63062931893e-05 0.0
loss 2.89101675044e-05 2.89101675044e-05 0.0
loss 4.23493606752e-05 4.23493606752e-05 0.0
loss 4.42191151349e-05 4.42191151349e-05 0.0
loss 6.43166049129e-05 6.43166049129e-05 0.0
loss 2.84459229592e-05 2.84459229592e-05 0.0
loss 5.49526269736e-05 5.49526269736e-05 0.0
loss 2.9488310805e-05 2.9488310805e-05 0.0
loss 4.43655948551e-05 4.43655948551e-05 0.0
loss 4.53825552559e-05 4.53825552559e-05 0.0
loss 2.92033960859e-05 2.92033960859e-05 0.0
loss 3.97956864621e-05 3.97956864621e-05 0.0
loss 4.73215438187e-05 4.73215438187e-05 0.0
loss 2.85550788425e-05 2.85550788425e-05 0.0
loss 4.12013294077e-05 4.12013294077e-05 0.0
loss 5.13575271411e-05 5.13575271411e-05 0.0
loss 2.79746687144e-05 2.79746687144e-05 0.0
loss 3.62721749896e-05 3.62721749896e-05 0.0
loss 2.59214

loss 1.4345750162e-05 1.4345750162e-05 0.0
loss 1.2031751767e-05 1.2031751767e-05 0.0
loss 1.30944884684e-05 1.30944884684e-05 0.0
loss 1.26325320153e-05 1.26325320153e-05 0.0
loss 1.46757226761e-05 1.46757226761e-05 0.0
loss 1.21327355266e-05 1.21327355266e-05 0.0
loss 1.22469388192e-05 1.22469388192e-05 0.0
loss 1.33722182989e-05 1.33722182989e-05 0.0
loss 1.5129756219e-05 1.5129756219e-05 0.0
loss 1.28077615708e-05 1.28077615708e-05 0.0
loss 1.52992417214e-05 1.52992417214e-05 0.0
loss 1.27570130373e-05 1.27570130373e-05 0.0
loss 1.21008028395e-05 1.21008028395e-05 0.0
loss 1.35870745314e-05 1.35870745314e-05 0.0
loss 1.36340589168e-05 1.36340589168e-05 0.0
loss 1.25104937885e-05 1.25104937885e-05 0.0
loss 1.31224716509e-05 1.31224716509e-05 0.0
loss 1.15658433902e-05 1.15658433902e-05 0.0
loss 1.26464075215e-05 1.26464075215e-05 0.0
loss 1.29441600037e-05 1.29441600037e-05 0.0
loss 1.38107792628e-05 1.38107792628e-05 0.0
loss 1.22871271267e-05 1.22871271267e-05 0.0
loss 1.336358362

loss 8.44344700847e-06 8.44344700847e-06 0.0
loss 9.16307613302e-06 9.16307613302e-06 0.0
loss 7.68109271114e-06 7.68109271114e-06 0.0
loss 7.34242243757e-06 7.34242243757e-06 0.0
loss 9.10703373201e-06 9.10703373201e-06 0.0
loss 7.64944425443e-06 7.64944425443e-06 0.0
loss 8.91844408276e-06 8.91844408276e-06 0.0
loss 7.96463936721e-06 7.96463936721e-06 0.0
loss 7.50256502144e-06 7.50256502144e-06 0.0
loss 7.96643595839e-06 7.96643595839e-06 0.0
loss 8.18032691453e-06 8.18032691453e-06 0.0
loss 8.22835722821e-06 8.22835722821e-06 0.0
loss 7.50185417957e-06 7.50185417957e-06 0.0
loss 8.66333818162e-06 8.66333818162e-06 0.0
loss 7.54547995292e-06 7.54547995292e-06 0.0
loss 8.15138463452e-06 8.15138463452e-06 0.0
loss 7.3090652911e-06 7.3090652911e-06 0.0
loss 7.3400168051e-06 7.3400168051e-06 0.0
loss 7.76013443261e-06 7.76013443261e-06 0.0
loss 7.5269308883e-06 7.5269308883e-06 0.0
loss 8.0279238309e-06 8.0279238309e-06 0.0
loss 7.29235710853e-06 7.29235710853e-06 0.0
loss 7.64955585167

loss 4.75116434589e-06 4.75116434589e-06 0.0
loss 4.69315343116e-06 4.69315343116e-06 0.0
loss 4.77175135485e-06 4.77175135485e-06 0.0
loss 4.71310994094e-06 4.71310994094e-06 0.0
loss 4.75319390515e-06 4.75319390515e-06 0.0
loss 4.80900265792e-06 4.80900265792e-06 0.0
loss 4.64722014456e-06 4.64722014456e-06 0.0
loss 4.73622439612e-06 4.73622439612e-06 0.0
loss 4.70919942421e-06 4.70919942421e-06 0.0
loss 4.7152307607e-06 4.7152307607e-06 0.0
loss 4.79577178001e-06 4.79577178001e-06 0.0
loss 4.63952318222e-06 4.63952318222e-06 0.0
loss 4.77274552971e-06 4.77274552971e-06 0.0
loss 4.64128686045e-06 4.64128686045e-06 0.0
loss 4.78412475884e-06 4.78412475884e-06 0.0
loss 4.63897746533e-06 4.63897746533e-06 0.0
loss 4.74173269654e-06 4.74173269654e-06 0.0
loss 4.64210967589e-06 4.64210967589e-06 0.0
loss 4.67360660191e-06 4.67360660191e-06 0.0
loss 4.76647570317e-06 4.76647570317e-06 0.0
loss 4.63565486105e-06 4.63565486105e-06 0.0
loss 4.71621299229e-06 4.71621299229e-06 0.0
loss 4.72157

...

loss 2.69750907765e-06 2.69750907765e-06 0.0
loss 2.69737969906e-06 2.69737969906e-06 0.0
loss 2.69730480022e-06 2.69730480022e-06 0.0
loss 2.69721781498e-06 2.69721781498e-06 0.0
loss 2.69731281575e-06 2.69731281575e-06 0.0
loss 2.69727388385e-06 2.69727388385e-06 0.0
loss 2.69728182399e-06 2.69728182399e-06 0.0
loss 2.69722485265e-06 2.69722485265e-06 0.0
loss 2.69724258552e-06 2.69724258552e-06 0.0
loss 2.69727172659e-06 2.69727172659e-06 0.0
loss 2.69720159212e-06 2.69720159212e-06 0.0
loss 2.69717962739e-06 2.69717962739e-06 0.0
loss 2.69726113422e-06 2.69726113422e-06 0.0
loss 2.69737175323e-06 2.69737175323e-06 0.0
loss 2.69723362747e-06 2.69723362747e-06 0.0
loss 2.69739475854e-06 2.69739475854e-06 0.0
loss 2.69718034639e-06 2.69718034639e-06 0.0
loss 2.69707505514e-06 2.69707505514e-06 0.0
loss 2.69692800674e-06 2.69692800674e-06 0.0
loss 2.69722312318e-06 2.69722312318e-06 0.0
loss 2.69719118751e-06 2.69719118751e-06 0.0
loss 2.69721316522e-06 2.69721316522e-06 0.0
loss 2.697

loss 2.69599777063e-06 2.69599777063e-06 0.0
loss 2.69600957401e-06 2.69600957401e-06 0.0
loss 2.69597473623e-06 2.69597473623e-06 0.0
loss 2.69593730313e-06 2.69593730313e-06 0.0
loss 2.69602489765e-06 2.69602489765e-06 0.0
loss 2.69607498577e-06 2.69607498577e-06 0.0
loss 2.69606721849e-06 2.69606721849e-06 0.0
loss 2.6959207863e-06 2.6959207863e-06 0.0
loss 2.6959920152e-06 2.6959920152e-06 0.0
loss 2.69597262647e-06 2.69597262647e-06 0.0
loss 2.6961144626e-06 2.6961144626e-06 0.0
loss 2.69597539171e-06 2.69597539171e-06 0.0
loss 2.69599148479e-06 2.69599148479e-06 0.0
loss 2.69601563102e-06 2.69601563102e-06 0.0
loss 2.69595019089e-06 2.69595019089e-06 0.0
loss 2.69605556328e-06 2.69605556328e-06 0.0
loss 2.6960535413e-06 2.6960535413e-06 0.0
loss 2.69606713816e-06 2.69606713816e-06 0.0
loss 2.69597042278e-06 2.69597042278e-06 0.0
loss 2.69595769151e-06 2.69595769151e-06 0.0
loss 2.69602990405e-06 2.69602990405e-06 0.0
loss 2.69600258208e-06 2.69600258208e-06 0.0
loss 2.69608490515

loss 2.69580041437e-06 2.69580041437e-06 0.0
loss 2.69579723696e-06 2.69579723696e-06 0.0
loss 2.69580420465e-06 2.69580420465e-06 0.0
loss 2.6958012895e-06 2.6958012895e-06 0.0
loss 2.69582738298e-06 2.69582738298e-06 0.0
loss 2.6957988378e-06 2.6957988378e-06 0.0
loss 2.69581343227e-06 2.69581343227e-06 0.0
loss 2.69580954394e-06 2.69580954394e-06 0.0
loss 2.69578161579e-06 2.69578161579e-06 0.0
loss 2.69578499788e-06 2.69578499788e-06 0.0
loss 2.69582028091e-06 2.69582028091e-06 0.0
loss 2.69579609055e-06 2.69579609055e-06 0.0
loss 2.69578859516e-06 2.69578859516e-06 0.0
loss 2.69581816368e-06 2.69581816368e-06 0.0
loss 2.69579527855e-06 2.69579527855e-06 0.0
loss 2.69579830575e-06 2.69579830575e-06 0.0
loss 2.69578074225e-06 2.69578074225e-06 0.0
loss 2.69578859941e-06 2.69578859941e-06 0.0
loss 2.69578001237e-06 2.69578001237e-06 0.0
loss 2.6957898526e-06 2.6957898526e-06 0.0
loss 2.69578016505e-06 2.69578016505e-06 0.0
loss 2.69577785922e-06 2.69577785922e-06 0.0
loss 2.695789466

loss 2.69574311719e-06 2.69574311719e-06 0.0
loss 2.69573742244e-06 2.69573742244e-06 0.0
loss 2.69573754861e-06 2.69573754861e-06 0.0
loss 2.69574166999e-06 2.69574166999e-06 0.0
loss 2.69573467109e-06 2.69573467109e-06 0.0
loss 2.6957409006e-06 2.6957409006e-06 0.0
loss 2.69573402939e-06 2.69573402939e-06 0.0
loss 2.69573398506e-06 2.69573398506e-06 0.0
loss 2.69573127187e-06 2.69573127187e-06 0.0
loss 2.69573159518e-06 2.69573159518e-06 0.0
loss 2.69573556397e-06 2.69573556397e-06 0.0
loss 2.69573824972e-06 2.69573824972e-06 0.0
loss 2.6957366045e-06 2.6957366045e-06 0.0
loss 2.69573588035e-06 2.69573588035e-06 0.0
loss 2.695733264e-06 2.695733264e-06 0.0
loss 2.69573347364e-06 2.69573347364e-06 0.0
loss 2.69574077858e-06 2.69574077858e-06 0.0
loss 2.69573419246e-06 2.69573419246e-06 0.0
loss 2.69573345362e-06 2.69573345362e-06 0.0
loss 2.69573189758e-06 2.69573189758e-06 0.0
loss 2.69573105492e-06 2.69573105492e-06 0.0
loss 2.69573328269e-06 2.69573328269e-06 0.0
loss 2.69572998892

loss 2.69571333655e-06 2.69571333655e-06 0.0
loss 2.69571668237e-06 2.69571668237e-06 0.0
loss 2.69571335034e-06 2.69571335034e-06 0.0
loss 2.69571202848e-06 2.69571202848e-06 0.0
loss 2.69571237716e-06 2.69571237716e-06 0.0
loss 2.6957115052e-06 2.6957115052e-06 0.0
loss 2.69571454502e-06 2.69571454502e-06 0.0
loss 2.69571001401e-06 2.69571001401e-06 0.0
loss 2.69571070933e-06 2.69571070933e-06 0.0
loss 2.69571389864e-06 2.69571389864e-06 0.0
loss 2.69571430959e-06 2.69571430959e-06 0.0
loss 2.69571257223e-06 2.69571257223e-06 0.0
loss 2.69570985689e-06 2.69570985689e-06 0.0
loss 2.69571053676e-06 2.69571053676e-06 0.0
loss 2.69571334705e-06 2.69571334705e-06 0.0
loss 2.69571054571e-06 2.69571054571e-06 0.0
loss 2.69571418879e-06 2.69571418879e-06 0.0
loss 2.69571398984e-06 2.69571398984e-06 0.0
loss 2.69570881422e-06 2.69570881422e-06 0.0
loss 2.69570789718e-06 2.69570789718e-06 0.0
loss 2.69571423366e-06 2.69571423366e-06 0.0
loss 2.69571156023e-06 2.69571156023e-06 0.0
loss 2.69571

In [60]:
params_output = [(8.9710060363567114e-07, np.array([ -4.18353755e+00,  -9.63668936e-03,  -1.00171035e+02,
         1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
         2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
         1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
         1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
        -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
         4.64461212e+00,   3.23329113e-01,   5.82061842e-02]))]

In [73]:
params_output = [(8.829397265807305e-07, np.array([ -4.33954858e+00,  -1.02215197e-02,  -1.12590032e+02,
         3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
         2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
         1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
         1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
        -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
         4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
         3.46319317e+00]))]

In [114]:
params_output = [(8.7421414571196454e-07, np.array([ -4.31249172e+00,  -9.93971047e-03,  -3.76018390e+01,
        -1.14759006e+02,   1.72557600e+01,   2.66437414e+01,
        -1.50817090e+01,   2.22342349e+01,  -3.62963119e+00,
         1.62230813e+00,   1.18480877e+00,  -8.52354746e-01,
        -8.38460594e-01,   1.98957701e+00,  -8.86622667e-01,
         1.66082225e-03,  -1.54824194e+00,   1.39761513e+00,
        -5.06767503e+01,   4.47029066e+00,   9.10205250e-02,
         5.87302830e-02,   1.82639066e+00]))]

In [39]:
params_output = [(8.8257346852300666e-07, np.array([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
        -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
        -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
         2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
        -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
         2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
        -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
         5.51658454e-02,   1.58601447e+00]))]

In [40]:
params_output = [(2.8925274000958436e-06, np.array([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
         3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
        -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
        -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
         7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
        -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
         1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
         2.18327852e+00,   6.63152141e-02]))]

In [62]:
# convert lists of optimal parameters to dictionaries
params_optimal = []
for pars in params_output:
    #params_optimal.append(to_param_dict(pars, [2, 15, 4, 0]))
    params_optimal.append(to_param_dict(pars[1], stats['hyperparams']))

In [64]:
# store hyperparameters and output parameters in a single file
try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

no file


In [65]:
with open(os.path.join(working, 'params_store' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [66]:
retreived_params

[{'hyperparams': {u'edens': [2.5, 3.1000000000000001, 3.5, 4.9000000000000004],
   u'pair': [2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003]},
  'params': {'edens': array([-43.2896107 ,   4.64461212,   0.32332911,   0.05820618]),
   'embed': array([-4.18353755, -0.00963669]),
   'lrcorr': array([], dtype=float64),
   'pair': array([ -1.00171035e+02,   1.90025394e+01,   2.15938317e+01,
           -1.39759833e+01,   2.16332289e+01,  -3.29542126e+00,
            1.70455674e+00,   1.41347064e+00,  -9.02958785e-01,
           -8.62309098e-01,   1.95964588e+00,  -8.70527088e-01,
            3.22342700e-02,  -1.53866121e+00,   1.37095441e+00])}}]